In [1]:
%env TOKENIZERS_PARALLELISM=false
!pip install --quiet keybert
print('pip installed keybert')

env: TOKENIZERS_PARALLELISM=false
pip installed keybert


In [2]:
import re
import pandas as pd
from datetime import datetime
from time import mktime

def clean(arg:str) -> str:
    return re.sub('[^a-zA-Z0-9. /,]', ' ', arg)

def short_review(arg: str) -> str:
    pieces = arg.split()
    return ' '.join(pieces[:20]) + '...'

# https://stackoverflow.com/a/6451892
def since(date):
    return mktime(date.timetuple())

def year_fraction(date) -> float:
    this_year = datetime(year=date.year, month=1, day=1)
    next_year = datetime(year=1 + date.year, month=1, day=1)
    return date.year + (since(date) - since(this_year))/(since(next_year) - since(this_year))

filename = '/kaggle/input/cyberpunk-2077-steam-reviews/cyberpunk_2077_filtered.csv'
usecols = ['language', 'review', 'updated']
df = pd.read_csv(filepath_or_buffer=filename, parse_dates=['updated'], usecols=usecols)
# let's only look at reviews in English 
df = df[df['language'] == 'english']
# not all non-English reviews are labeled correctly
# and we want to remove emoji
# so we need to work a little harder
df['clean'] = df['review'].apply(func=clean)
# we need to be mindful of review length
df['token count'] = df['clean'].str.split().str.len()
df = df[df['token count'] > 3]
# we want to be able to get time slices
df['year'] = df['updated'].apply(func=year_fraction) 
df = df.drop(columns=['language', 'updated'])
# we need to truncate the review we show in the plot
df['short review'] = df['review'].apply(func=short_review)
df.head()

review  \
0   It's very fun. I don't usually like open world...   
6   Coming back to try the game after 2.0 came out...   
10  i dont even own this fucking game why can i wr...   
11  Todo valio la pena al final con el mejor endin...   
12  I am a sneaky boi and I stab people with arm s...   

                                                clean  token count  \
0   It s very fun. I don t usually like open world...           42   
6   Coming back to try the game after 2.0 came out...           80   
10  i dont even own this fucking game why can i wr...           13   
11  Todo valio la pena al final con el mejor endin...           50   
12  I am a sneaky boi and I stab people with arm s...           13   

           year                                       short review  
0   2023.947945  It's very fun. I don't usually like open world...  
6   2023.947945  Coming back to try the game after 2.0 came out...  
10  2023.947945  i dont even own this fucking game why can i wr...  
11  2023.947945  Todo valio la pena al final con el mejor endin...  
12  2023.947945  I am a sneaky boi and I stab people with arm s...

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 227200 entries, 0 to 612379
Data columns (total 5 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   review        227200 non-null  object 
 1   clean         227200 non-null  object 
 2   token count   227200 non-null  int64  
 3   year          227200 non-null  float64
 4   short review  227200 non-null  object 
dtypes: float64(1), int64(1), object(3)
memory usage: 10.4+ MB


In [4]:
from plotly.express import histogram
histogram(data_frame=df, x='year', log_y=True).show()

Those spikes are really something; we might expect them to correlate with events like updates or minor releases, maybe?

In [5]:
histogram(data_frame=df, x='token count', log_y=True).show()

Our BERT models expect sequences of 128 subwords by default; review length measured in tokens may be an issue we need to deal with.

In [6]:
# let's take a fixed number of rows starting with the most recent going back in time
sample_df = df.sort_values(ascending=False, by='year').head(n=10000)
sample_df.shape

(10000, 5)

In [7]:
histogram(data_frame=sample_df, x='token count', log_y=True).show()

In [8]:
# use KeyBERT to tag using the top keyword
from arrow import now
from keybert import KeyBERT

COLUMN = 'clean'
MODEL = 'all-MiniLM-L12-v2'
model = KeyBERT(model=MODEL)
# if we set this to 512 we get about 99% of the input intact
model.max_seq_length = 512

model_start = now()
document_embeddings, word_embeddings = model.extract_embeddings(docs=sample_df[COLUMN].values,)
print('embedding time: {}'.format(now() - model_start))
keywords = model.extract_keywords(docs=sample_df[COLUMN].values, top_n=1)
print('model time: {}'.format(now() - model_start))

.gitattributes:   0%|          | 0.00/1.18k [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.6k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/573 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/352 [00:00<?, ?B/s]

train_script.py:   0%|          | 0.00/13.2k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

embedding time: 0:04:06.269629
model time: 0:08:17.836191


In [9]:
TOP_N = 26 # we have 26 colors so let's use 26 tags
# we are folding together some similar tags somewhat arbitrarily
# this is mostly plural->singular but also 
# accounting for the fact that the game has a two-word name
RESOLVE = {'buggy' : 'bug', 'bugs': 'bug', 
           'crashes': 'crash', 'crashing': 'crash',
           'games': 'game', 'gameplay': 'game',
           '2077': 'cyberpunk',
           'updates': 'update',
          }

sample_df['top keyword'] = [item[0][0] if len(item) else 'unknown' for item in keywords]
sample_df['tag'] = sample_df['top keyword'].apply(func=lambda x: x if x not in RESOLVE.keys() else RESOLVE[x])
# all of the keywords out of the top N get retagged as unknown
sample_df['tag'] = sample_df['tag'].apply(func=lambda x: 'unknown' if x not in sample_df['tag'].value_counts()[:TOP_N].index.tolist() else x)
# how much of the corpus did we tag?
print(sample_df['tag'].value_counts(normalize=True))
print(sorted(sample_df['tag'].unique().tolist()))

tag
unknown      0.5216
game         0.1113
cyberpunk    0.0886
dlc          0.0307
phantom      0.0294
bug          0.0261
cdpr         0.0258
crash        0.0159
launch       0.0156
witcher      0.0146
rpg          0.0123
gta          0.0100
update       0.0094
glitches     0.0082
night        0.0079
patch        0.0077
release      0.0068
immersive    0.0068
hours        0.0065
review       0.0064
keanu        0.0063
starfield    0.0061
panam        0.0056
samurai      0.0055
fun          0.0051
fixed        0.0050
play         0.0048
Name: proportion, dtype: float64
['bug', 'cdpr', 'crash', 'cyberpunk', 'dlc', 'fixed', 'fun', 'game', 'glitches', 'gta', 'hours', 'immersive', 'keanu', 'launch', 'night', 'panam', 'patch', 'phantom', 'play', 'release', 'review', 'rpg', 'samurai', 'starfield', 'unknown', 'update', 'witcher']


In [10]:
from plotly.colors import qualitative
from plotly.express import scatter
from umap import UMAP

umap_model = UMAP(n_components=2, random_state=2023, verbose=True, n_jobs=1)
sample_df[['u0', 'u1']] = umap_model.fit_transform(X=document_embeddings)
scatter(data_frame=sample_df, x='u0', y='u1', hover_name='short review',
        hover_data = ['top keyword'],
        height=900, color='tag', color_discrete_sequence=qualitative.Alphabet).show()

UMAP(n_jobs=1, random_state=2023, verbose=True)
Thu Jan  4 17:41:08 2024 Construct fuzzy simplicial set
Thu Jan  4 17:41:08 2024 Finding Nearest Neighbors
Thu Jan  4 17:41:08 2024 Building RP forest with 10 trees
Thu Jan  4 17:41:12 2024 NN descent for 13 iterations
	 1  /  13
	 2  /  13
	 3  /  13
	 4  /  13
	 5  /  13
	 6  /  13
	Stopping threshold met -- exiting after 6 iterations
Thu Jan  4 17:41:26 2024 Finished Nearest Neighbor Search
Thu Jan  4 17:41:29 2024 Construct embedding


Epochs completed:   0%|            0/500 [00:00]

	completed  0  /  500 epochs
	completed  50  /  500 epochs
	completed  100  /  500 epochs
	completed  150  /  500 epochs
	completed  200  /  500 epochs
	completed  250  /  500 epochs
	completed  300  /  500 epochs
	completed  350  /  500 epochs
	completed  400  /  500 epochs
	completed  450  /  500 epochs
Thu Jan  4 17:41:40 2024 Finished embedding


In [11]:
from collections import Counter
print(Counter(' '.join(sample_df['clean'].values.tolist())))

Counter({' ': 766310, 'e': 336972, 't': 255829, 'a': 227897, 'o': 195144, 'i': 188636, 'n': 178395, 's': 169056, 'r': 144135, 'h': 132070, 'l': 119582, 'd': 97483, 'm': 85365, 'u': 83436, 'g': 80550, 'y': 73952, 'c': 68200, 'p': 54838, 'f': 53424, 'w': 46283, 'b': 44287, '.': 42088, 'v': 33006, ',': 28419, 'k': 24078, 'I': 20368, 'T': 11078, '0': 9347, 'C': 8101, 'A': 7162, 'x': 6912, 'P': 6866, '2': 6323, 'S': 5807, 'D': 5696, 'j': 5674, 'R': 4787, 'E': 4725, '1': 4658, 'G': 4588, 'L': 4521, 'N': 4433, 'O': 3559, '/': 3519, 'W': 3063, '7': 2967, 'M': 2922, 'q': 2825, 'z': 2739, 'B': 2643, '3': 2229, 'H': 2211, 'Y': 2124, 'F': 2053, 'U': 1592, 'V': 1588, '5': 1252, 'J': 1038, '4': 897, 'K': 871, '6': 822, '9': 759, '8': 698, 'X': 391, 'Q': 167, 'Z': 87})
